### Heatmap

In [3]:
import plotly.graph_objects as go
import numpy as np
from scipy.interpolate import griddata
from PIL import Image

# Puntos de medición (x, y, señal_dbm)
puntos = np.array([
    [1, 1, -30],
    [5, 1, -45],
    [1, 5, -50],
    [5, 5, -70],
    [3, 3, -40],
])

x = puntos[:, 0]
y = puntos[:, 1]
z = puntos[:, 2]

# Crear grid interpolado
xi = np.linspace(x.min(), x.max(), 100)
yi = np.linspace(y.min(), y.max(), 100)
xi, yi = np.meshgrid(xi, yi)
zi = griddata((x, y), z, (xi, yi), method='cubic')

# Cargar imagen del plano de la habitación
img = Image.open("plano_habitacion.png")

fig = go.Figure()

# Imagen de fondo (plano)
fig.add_layout_image(
    source=img,
    x=x.min(), y=y.max(),
    sizex=x.max() - x.min(),
    sizey=y.max() - y.min(),
    xref="x", yref="y",
    layer="below",
    opacity=0.5,
)

# Heatmap de señal WiFi
fig.add_trace(go.Heatmap(
    x=xi[0], y=yi[:, 0], z=zi,
    colorscale="RdYlGn",
    reversescale=False,
    opacity=0.6,
    colorbar=dict(title="dBm"),
    hovertemplate="X: %{x:.1f}m<br>Y: %{y:.1f}m<br>Señal: %{z:.0f} dBm<extra></extra>",
))

# Puntos de medición
fig.add_trace(go.Scatter(
    x=x, y=y, mode='markers',
    marker=dict(size=10, color='black', symbol='x'),
    name='Puntos de medición',
    text=[f"{v} dBm" for v in z],
))

fig.update_layout(
    title="Heatmap WiFi - Habitación",
    xaxis_title="X (metros)",
    yaxis_title="Y (metros)",
    xaxis=dict(scaleanchor="y"),
    width=800, height=600,
)

fig.show()
# fig.write_html("wifi_heatmap.html")  # Exportar como HTML interactivo

In [30]:
import folium
from folium.plugins import HeatMap
from PIL import Image

# Carga la imagen del plano
img_path = "plano_habitacion.png"
img = Image.open(img_path)
width, height = img.size

# Sistema de coordenadas simple (pixeles), sin tiles de fondo
m = folium.Map(
    location=[height / 2, width / 2],
    zoom_start=0,
    crs="Simple",
    tiles=None,
    max_zoom=5,
    min_zoom=-2,
    max_bounds=True,
    width='100%',
    height='100%',
)

# Superponer imagen como mapa base
folium.raster_layers.ImageOverlay(
    image=img_path,
    bounds=[[0, 0], [height, width]],
    opacity=1.0,
    interactive=False
).add_to(m)

# Centrar y ajustar la vista exactamente a la imagen
bounds = [[0, 0], [height, width]]
m.fit_bounds(bounds, padding=[0, 0])

# Evitar desplazarse fuera del plano
m.options["maxBounds"] = bounds
m.options["maxBoundsViscosity"] = 1.0

# Datos de calor en coordenadas de la imagen (y, x, intensidad)
data = [
    [height * 0.2, width * 0.3, 0.9],
    [height * 0.5, width * 0.5, 0.6],
    [height * 0.7, width * 0.7, 0.8],
    [height * 0.8, width * 0.3, 0.7],
    [height * 0.3, width * 0.8, 0.5],
]

HeatMap(
    data,
    radius=100,
    blur=40,
    min_opacity=0.0,
    max_zoom=5,
).add_to(m)

# Fondo blanco para evitar gris por defecto
m.get_root().html.add_child(folium.Element(
    "<style>html, body, .folium-map {background: white !important;}</style>"
))

# Guardar como HTML y abrir en navegador
m.save("heatmap.html")

In [31]:
# ...existing code...
import numpy as np
import plotly.graph_objects as go
from scipy.interpolate import griddata
from PIL import Image

# Cargar imagen del plano
img_path = "plano_habitacion.png"
img = Image.open(img_path)
width, height = img.size

# Datos en coordenadas de imagen (x, y, intensidad)
puntos = np.array([
    [width * 0.2, height * 0.3, 0.9],
    [width * 0.5, height * 0.5, 0.6],
    [width * 0.7, height * 0.7, 0.8],
    [width * 0.3, height * 0.8, 0.7],
    [width * 0.8, height * 0.3, 0.5],
])

x = puntos[:, 0]
y = puntos[:, 1]
z = puntos[:, 2]

# Interpolación suave
xi = np.linspace(0, width, 200)
yi = np.linspace(0, height, 200)
xi, yi = np.meshgrid(xi, yi)
zi = griddata((x, y), z, (xi, yi), method="cubic")

fig = go.Figure()

# Fondo: plano
fig.add_layout_image(
    dict(
        source=img,
        x=0, y=height,
        sizex=width, sizey=height,
        xref="x", yref="y",
        layer="below"
    )
)

# Heatmap
fig.add_trace(go.Heatmap(
    x=xi[0], y=yi[:, 0], z=zi,
    colorscale="Turbo",
    opacity=0.6,
    colorbar=dict(title="Intensidad"),
    hovertemplate="X: %{x:.0f}px<br>Y: %{y:.0f}px<br>Val: %{z:.2f}<extra></extra>"
))

# Puntos
fig.add_trace(go.Scatter(
    x=x, y=y, mode="markers",
    marker=dict(size=8, color="black", symbol="x"),
    name="Puntos"
))

fig.update_layout(
    title="Heatmap sobre plano",
    xaxis=dict(range=[0, width], scaleanchor="y", visible=False),
    yaxis=dict(range=[0, height], autorange="reversed", visible=False),
    width=800, height=600
)

fig.show()
# ...existing code...

In [32]:
# ...existing code...
import numpy as np
import plotly.graph_objects as go
from scipy.interpolate import griddata
from PIL import Image

# Cargar imagen del plano
img_path = "plano_habitacion.png"
img = Image.open(img_path)
width, height = img.size

# Datos (x, y, intensidad) en pixeles
puntos = np.array([
    [width * 0.15, height * 0.20, 0.9],
    [width * 0.50, height * 0.35, 0.7],
    [width * 0.80, height * 0.25, 0.6],
    [width * 0.30, height * 0.70, 0.8],
    [width * 0.65, height * 0.85, 0.5],
])

x = puntos[:, 0]
y = puntos[:, 1]
z = puntos[:, 2]

# Interpolación para suavizar el heatmap
xi = np.linspace(0, width, 300)
yi = np.linspace(0, height, 300)
xi, yi = np.meshgrid(xi, yi)
zi = griddata((x, y), z, (xi, yi), method="cubic")

fig = go.Figure()

# Imagen de fondo
fig.add_layout_image(
    dict(
        source=img,
        x=0, y=height,
        sizex=width, sizey=height,
        xref="x", yref="y",
        layer="below"
    )
)

# Heatmap
fig.add_trace(go.Heatmap(
    x=xi[0], y=yi[:, 0], z=zi,
    colorscale="Turbo",
    opacity=0.7,
    zmin=0, zmax=1,
    colorbar=dict(title="Intensidad"),
    hovertemplate="X: %{x:.0f}px<br>Y: %{y:.0f}px<br>Val: %{z:.2f}<extra></extra>"
))

# Puntos de medición
fig.add_trace(go.Scatter(
    x=x, y=y, mode="markers",
    marker=dict(size=8, color="black", symbol="x"),
    name="Puntos"
))

fig.update_layout(
    title="Heatmap WiFi sobre plano",
    xaxis=dict(range=[0, width], scaleanchor="y", visible=False),
    yaxis=dict(range=[0, height], autorange="reversed", visible=False),
    width=900, height=650,
    margin=dict(l=0, r=0, t=40, b=0),
)

fig.show()
# ...existing code...

In [33]:
import plotly.graph_objects as go
from PIL import Image
import numpy as np

# Cargar imagen
img = Image.open("plano_habitacion.png")
width, height = img.size

# Datos de ejemplo (clics o miradas)
np.random.seed(1)
x = np.random.randint(0, width, 300)
y = np.random.randint(0, height, 300)

fig = go.Figure()

# Heatmap
fig.add_trace(go.Histogram2d(
    x=x,
    y=y,
    nbinsx=60,
    nbinsy=40,
    colorscale="Jet",
    showscale=True,
    opacity=0.6
))

# Imagen de fondo
fig.add_layout_image(
    dict(
        source=img,
        x=0,
        y=0,
        sizex=width,
        sizey=height,
        xref="x",
        yref="y",
        sizing="stretch",
        layer="below"
    )
)

fig.update_layout(
    xaxis=dict(range=[0, width], visible=False),
    yaxis=dict(range=[height, 0], visible=False),
    width=width,
    height=height
)

fig.show()


In [34]:
import numpy as np
import plotly.graph_objects as go
from scipy.ndimage import gaussian_filter
from scipy.interpolate import griddata
from PIL import Image
import base64
from io import BytesIO

# Cargar imagen del plano
img_path = "plano_habitacion.png"
img = Image.open(img_path)
width, height = img.size

# Convertir imagen a base64 para Plotly
buffer = BytesIO()
img.save(buffer, format="PNG")
img_base64 = "data:image/png;base64," + base64.b64encode(buffer.getvalue()).decode()

# ========================================
# Datos de medición (x_px, y_px, intensidad)
# Reemplaza con tus datos reales
# ========================================
puntos = np.array([
    [width * 0.15, height * 0.20, 0.95],
    [width * 0.25, height * 0.35, 0.85],
    [width * 0.50, height * 0.35, 0.70],
    [width * 0.80, height * 0.25, 0.60],
    [width * 0.30, height * 0.60, 0.80],
    [width * 0.20, height * 0.75, 0.75],
    [width * 0.65, height * 0.80, 0.50],
    [width * 0.45, height * 0.50, 0.65],
    [width * 0.70, height * 0.55, 0.55],
    [width * 0.10, height * 0.50, 0.90],
])

x = puntos[:, 0]
y = puntos[:, 1]
z = puntos[:, 2]

# ========================================
# Interpolación + suavizado gaussiano
# ========================================
resolution = 300  # resolución del grid
xi = np.linspace(0, width, resolution)
yi = np.linspace(0, height, resolution)
xi_grid, yi_grid = np.meshgrid(xi, yi)

# Interpolar valores en todo el grid
zi = griddata((x, y), z, (xi_grid, yi_grid), method="cubic", fill_value=0)

# Aplicar suavizado gaussiano (sigma alto = más difuminado, estilo eye-tracking)
sigma = 15  # Ajusta: más alto → más suave y difuminado
zi_smooth = gaussian_filter(zi, sigma=sigma)

# Normalizar entre 0 y 1
zi_smooth = (zi_smooth - zi_smooth.min()) / (zi_smooth.max() - zi_smooth.min())

# ========================================
# Crear máscara de transparencia (ocultar zonas sin datos)
# ========================================
# Las zonas con valor muy bajo se hacen transparentes
threshold = 0.05
zi_display = np.where(zi_smooth > threshold, zi_smooth, np.nan)

# ========================================
# Colorscale personalizada estilo eye-tracking
# Verde → Amarillo → Rojo (como la imagen de referencia)
# ========================================
colorscale_eyetracking = [
    [0.0, "rgba(0, 128, 0, 0.0)"],      # Transparente
    [0.15, "rgba(0, 128, 0, 0.3)"],      # Verde suave
    [0.3, "rgba(0, 200, 0, 0.5)"],       # Verde
    [0.45, "rgba(144, 238, 0, 0.6)"],    # Verde-amarillo
    [0.6, "rgba(255, 255, 0, 0.7)"],     # Amarillo
    [0.75, "rgba(255, 165, 0, 0.8)"],    # Naranja
    [0.9, "rgba(255, 69, 0, 0.85)"],     # Rojo-naranja
    [1.0, "rgba(255, 0, 0, 0.9)"],       # Rojo intenso
]

# ========================================
# Figura interactiva
# ========================================
fig = go.Figure()

# Imagen de fondo (plano)
fig.add_layout_image(
    dict(
        source=img_base64,
        x=0, y=0,
        sizex=width, sizey=height,
        xref="x", yref="y",
        sizing="stretch",
        layer="below",
        opacity=1.0,
    )
)

# Heatmap suavizado estilo eye-tracking
fig.add_trace(go.Heatmap(
    x=xi,
    y=yi,
    z=zi_display,
    colorscale=colorscale_eyetracking,
    zmin=0, zmax=1,
    opacity=0.7,
    showscale=True,
    colorbar=dict(
        title=dict(text="Intensidad", side="right"),
        thickness=15,
        len=0.6,
        tickvals=[0, 0.25, 0.5, 0.75, 1.0],
        ticktext=["Baja", "", "Media", "", "Alta"],
    ),
    hovertemplate=(
        "X: %{x:.0f} px<br>"
        "Y: %{y:.0f} px<br>"
        "Intensidad: %{z:.2f}<extra></extra>"
    ),
    connectgaps=False,
))

# Puntos de medición
fig.add_trace(go.Scatter(
    x=x, y=y,
    mode="markers+text",
    marker=dict(
        size=12,
        color="white",
        symbol="circle",
        line=dict(width=2, color="black"),
    ),
    text=[f"{v:.0%}" for v in z],
    textposition="top center",
    textfont=dict(size=10, color="black"),
    name="Puntos de medición",
    hovertemplate=(
        "Punto de medición<br>"
        "X: %{x:.0f} px<br>"
        "Y: %{y:.0f} px<br>"
        "Valor: %{text}<extra></extra>"
    ),
))

fig.update_layout(
    title=dict(
        text="🔥 Heatmap Interactivo - Estilo Eye-Tracking",
        font=dict(size=18),
    ),
    xaxis=dict(
        range=[0, width],
        visible=False,
        scaleanchor="y",
        constrain="domain",
    ),
    yaxis=dict(
        range=[height, 0],  # Invertir Y para que coincida con imagen
        visible=False,
        constrain="domain",
    ),
    width=900,
    height=int(900 * height / width),
    margin=dict(l=10, r=10, t=50, b=10),
    plot_bgcolor="white",
    # Botones interactivos
    updatemenus=[
        dict(
            type="buttons",
            direction="left",
            x=0.0, y=1.12,
            buttons=[
                dict(
                    label="Mostrar puntos",
                    method="update",
                    args=[{"visible": [True, True]}],
                ),
                dict(
                    label="Solo heatmap",
                    method="update",
                    args=[{"visible": [True, False]}],
                ),
            ],
        )
    ],
    # Slider para opacidad
    sliders=[
        dict(
            active=7,
            currentvalue=dict(prefix="Opacidad: ", suffix=""),
            pad=dict(t=40),
            steps=[
                dict(
                    method="restyle",
                    args=["opacity", [o / 10]],
                    label=f"{o / 10:.1f}",
                )
                for o in range(0, 11)
            ],
        )
    ],
)

fig.show()

# Exportar como HTML interactivo
fig.write_html("heatmap_eyetracking.html", include_plotlyjs=True)
print("✅ Exportado: heatmap_eyetracking.html")

✅ Exportado: heatmap_eyetracking.html


In [7]:
import numpy as np
import plotly.graph_objects as go
from scipy.ndimage import gaussian_filter
from scipy.interpolate import griddata
from PIL import Image
import base64
from io import BytesIO

# Cargar imagen del plano
img_path = "plano_habitacion.png"
img = Image.open(img_path)
width, height = img.size

# Convertir imagen a base64 para Plotly
buffer = BytesIO()
img.save(buffer, format="PNG")
img_base64 = "data:image/png;base64," + base64.b64encode(buffer.getvalue()).decode()

# ========================================
# Datos de medicion (x_px, y_px, potencia en dBm)
# Rango: -80 (bajo) a 0 (alto)
# ========================================
puntos = np.array([
    [width * 0.15, height * 0.20, -10],
    [width * 0.25, height * 0.35, -20],
    [width * 0.50, height * 0.35, -35],
    [width * 0.80, height * 0.25, -45],
    [width * 0.30, height * 0.60, -25],
    [width * 0.20, height * 0.75, -30],
    [width * 0.65, height * 0.80, -55],
    [width * 0.45, height * 0.50, -40],
    [width * 0.70, height * 0.55, -50],
    [width * 0.10, height * 0.50, -15],
])

x = puntos[:, 0]
y = puntos[:, 1]
z = puntos[:, 2]

# ========================================
# Interpolacion + suavizado gaussiano
# ========================================
resolution = 300  # resolucion del grid

xi = np.linspace(0, width, resolution)
yi = np.linspace(0, height, resolution)
xi_grid, yi_grid = np.meshgrid(xi, yi)

# Interpolar valores en todo el grid
zi = griddata((x, y), z, (xi_grid, yi_grid), method="cubic", fill_value=-80)

# Aplicar suavizado gaussiano (sigma alto = mas difuminado, estilo eye-tracking)
sigma = 15  # Ajusta: mas alto -> mas suave y difuminado
zi_smooth = gaussian_filter(zi, sigma=sigma)

# Normalizar para mascara de transparencia
zmin, zmax = -80.0, 0.0

zi_norm = (zi_smooth - zmin) / (zmax - zmin)
zi_norm = np.clip(zi_norm, 0, 1)

# ========================================
# Crear mascara de transparencia (ocultar zonas sin datos)
# ========================================
# Las zonas con valor muy bajo se hacen transparentes
threshold_norm = 0.05
zi_display = np.where(zi_norm > threshold_norm, zi_smooth, np.nan)

# Texto de hover con control de NaN
hover_text = np.empty_like(zi_display, dtype=object)
mask = np.isnan(zi_display)
hover_text[mask] = "RSSI: sin datos"
hover_text[~mask] = np.array([f"RSSI: {v:.1f} dBm" for v in zi_display[~mask]])

# ========================================
# Colorscale personalizada estilo eye-tracking
# Verde -> Amarillo -> Rojo (como la imagen de referencia)
# ========================================
colorscale_eyetracking = [
    [0.0, "rgba(0, 128, 0, 0.0)"],      # Transparente
    [0.15, "rgba(0, 128, 0, 0.3)"],      # Verde suave
    [0.3, "rgba(0, 200, 0, 0.5)"],       # Verde
    [0.45, "rgba(144, 238, 0, 0.6)"],    # Verde-amarillo
    [0.6, "rgba(255, 255, 0, 0.7)"],     # Amarillo
    [0.75, "rgba(255, 165, 0, 0.8)"],    # Naranja
    [0.9, "rgba(255, 69, 0, 0.85)"],     # Rojo-naranja
    [1.0, "rgba(255, 0, 0, 0.9)"],       # Rojo intenso
]

# ========================================
# Figura interactiva
# ========================================
fig = go.Figure()

# Imagen de fondo (plano)
fig.add_layout_image(
    dict(
        source=img_base64,
        x=0, y=0,
        sizex=width, sizey=height,
        xref="x", yref="y",
        sizing="stretch",
        layer="below",
        opacity=1.0,
    )
)

# Heatmap suavizado estilo eye-tracking
fig.add_trace(go.Heatmap(
    x=xi,
    y=yi,
    z=zi_display,
    text=hover_text,
    colorscale=colorscale_eyetracking,
    zmin=zmin, zmax=zmax,
    opacity=0.7,
    showscale=True,
    colorbar=dict(
        title=dict(text="Potencia (dBm)", side="right"),
        thickness=15,
        len=0.6,
        tickvals=[-80, -60, -40, -20, 0],
        ticktext=["-80", "-60", "-40", "-20", "0"],
    ),
    hovertemplate=(
        "X: %{x:.0f} px<br>"
        "Y: %{y:.0f} px<br>"
        "%{text}<extra></extra>"
    ),
    connectgaps=False,
))

# Puntos de medicion
fig.add_trace(go.Scatter(
    x=x, y=y,
    mode="markers+text",
    marker=dict(
        size=12,
        color="white",
        symbol="circle",
        line=dict(width=2, color="black"),
    ),
    text=[f"{v:.0f} dBm" for v in z],
    textposition="top center",
    textfont=dict(size=10, color="black"),
    name="Puntos de medicion",
    hovertemplate=(
        "Punto de medicion<br>"
        "X: %{x:.0f} px<br>"
        "Y: %{y:.0f} px<br>"
        "Valor: %{text}<extra></extra>"
    ),
))

fig.update_layout(
    title=dict(
        text="Heatmap",
        font=dict(size=18),
    ),
    xaxis=dict(
        range=[0, width],
        visible=False,
        scaleanchor="y",
        constrain="domain",
    ),
    yaxis=dict(
        range=[height, 0],  # Invertir Y para que coincida con imagen
        visible=False,
        constrain="domain",
    ),
    width=900,
    height=int(900 * height / width),
    margin=dict(l=10, r=10, t=50, b=10),
    plot_bgcolor="white",
    # Botones interactivos
    updatemenus=[
        dict(
            type="buttons",
            direction="left",
            x=0.4,
            buttons=[
                dict(
                    label="Mostrar puntos",
                    method="update",
                    args=[{"visible": [True, True]}],
                ),
                dict(
                    label="Solo heatmap",
                    method="update",
                    args=[{"visible": [True, False]}],
                ),
            ],
        )
    ],
    # Slider para opacidad
    sliders=[
        dict(
            active=7,
            currentvalue=dict(prefix="Opacidad: ", suffix=""),
            pad=dict(t=40),
            steps=[
                dict(
                    method="restyle",
                    args=["opacity", [o / 10]],
                    label=f"{o / 10:.1f}",
                )
                for o in range(0, 11)
            ],
        )
    ],
)

fig.show()